周内效应——定投篇

In [11]:
import pandas as pd
from datetime import datetime
import trdb2py
import numpy as np

isStaticImg = False
width = 960
height = 768

pd.options.display.max_columns = None
pd.options.display.max_rows = None

trdb2cfg = trdb2py.loadConfig('./trdb2.yaml')

In [18]:
# 具体基金
asset = 'jqdata.000300_XSHG|1d'
# baselineasset = 'jrj.510310'
# asset = 'jrj.110011'
# baselineasset = 'jqdata.000300_XSHG|1d'

# 起始时间，0表示从最开始算起
tsStart = 0
tsStart = int(trdb2py.str2timestamp('2013-05-01', '%Y-%m-%d'))

# 结束时间，-1表示到现在为止
tsEnd = -1
tsEnd = int(trdb2py.str2timestamp('2020-09-30', '%Y-%m-%d'))

# 初始资金池
paramsinit = trdb2py.trading2_pb2.InitParams(
    money=10000,
)

# 买入参数，用全部的钱来买入（也就是复利）
paramsbuy = trdb2py.trading2_pb2.BuyParams(
    perHandMoney=1,
)

# 买入参数，用全部的钱来买入（也就是复利）
paramsbuy2 = trdb2py.trading2_pb2.BuyParams(
    perHandMoney=0.5,
)

# 卖出参数，全部卖出
paramssell = trdb2py.trading2_pb2.SellParams(
    perVolume=1,
)

# 止盈参数，120%止盈
paramstakeprofit = trdb2py.trading2_pb2.TakeProfitParams(
    perVolume=1,
    isFinish=True,
)

# 卖出参数，全部卖出
paramssell7 = trdb2py.trading2_pb2.SellParams(
#     perVolume=1,
    keepTime=7 * 24 * 60 * 60,
)

lststart = [1, 2, 3, 4, 5]
lsttitle = ['周一', '周二', '周三', '周四', '周五']

In [13]:
def calcweekday2val2(wday, offday):
    if offday == 1:
        if wday == 5:
            return 3
    if offday == 2:
        if wday >= 4:
            return 4
    if offday == 3:
        if wday >= 3:
            return 5
    if offday == 4:
        if wday >= 2:
            return 6
        
    return offday


In [14]:
asset = 'jrj.110011'
asset = 'jqdata.000036_XSHG|1d'
asset = 'jqdata.000032_XSHG|1d'
asset = 'jqdata.000300_XSHG|1d'

# baseline    
s0 = trdb2py.trading2_pb2.Strategy(
    name="normal",
    asset=trdb2py.str2asset(asset),         
)
        
buy0 = trdb2py.trading2_pb2.CtrlCondition(
    name='buyandhold',
)

paramsbuy = trdb2py.trading2_pb2.BuyParams(
    perHandMoney=1,
)

paramsinit = trdb2py.trading2_pb2.InitParams(
    money=10000,
)

s0.buy.extend([buy0])
s0.paramsBuy.CopyFrom(paramsbuy)
s0.paramsInit.CopyFrom(paramsinit)        
p0 = trdb2py.trading2_pb2.SimTradingParams(
    assets=[trdb2py.str2asset(asset)],
    startTs=tsStart,
    endTs=tsEnd,
    strategies=[s0],
    title='沪深300',
)  

pnlBaseline = trdb2py.simTrading(trdb2cfg, p0)
trdb2py.showPNL(pnlBaseline, toImg=isStaticImg, width=width, height=height)

In [10]:
lstparams = []

for i in range(1, 28):
    buy0 = trdb2py.trading2_pb2.CtrlCondition(
        name='monthdayex',
        vals=[i],
    )

    s0 = trdb2py.trading2_pb2.Strategy(
        name="normal",
        asset=trdb2py.str2asset(asset),
    )
    
    paramsaip = trdb2py.trading2_pb2.AIPParams(
        money=10000,
        type=trdb2py.trading2_pb2.AIPTT_WEEKDAY,
        day=1,
    )

    s0.buy.extend([buy0])
    s0.paramsBuy.CopyFrom(paramsbuy)
    s0.paramsSell.CopyFrom(paramssell)
#     s0.paramsInit.CopyFrom(paramsinit)
    s0.paramsAIP.CopyFrom(paramsaip)
    lstparams.append(trdb2py.trading2_pb2.SimTradingParams(
        assets=[trdb2py.str2asset(asset)],
        startTs=tsStart,
        endTs=tsEnd,
        strategies=[s0],
        title='{}定投'.format(i),
    ))
 
lstaippnl = trdb2py.simTradings(trdb2cfg, lstparams)

trdb2py.showPNLs(lstaippnl + [pnlBaseline], toImg=isStaticImg, width=width, height=height)

我们看到不管是每个月的几号买入，最终其实都差异不大

In [15]:
dfpnl1b = trdb2py.buildPNLReport(lstaippnl + [pnlBaseline])

dfpnl1b[['title', 'maxDrawdown', 'maxDrawdownStart', 'maxDrawdownEnd', 'totalReturns', 'sharpe', 'annualizedReturns', 'annualizedVolatility', 'variance']].sort_values(by='totalReturns', ascending=False)

title  maxDrawdown maxDrawdownStart maxDrawdownEnd  totalReturns  \
27  沪深300     0.466961       2015-06-08     2016-01-28      1.874480   
26   26定投     0.448070       2015-06-08     2015-08-26      1.415818   
24   25定投     0.449069       2015-06-08     2015-08-26      1.413921   
25   27定投     0.447711       2015-06-08     2015-08-26      1.413895   
1     1定投     0.449423       2015-06-08     2015-08-26      1.409786   
21   24定投     0.450812       2015-06-08     2015-08-26      1.407142   
23   23定投     0.450856       2015-06-08     2015-08-26      1.406095   
8     9定投     0.450906       2015-06-08     2015-08-26      1.405714   
6     8定投     0.450081       2015-06-08     2015-08-26      1.404746   
16   18定投     0.452014       2015-06-08     2015-08-26      1.404034   
22   22定投     0.450326       2015-06-08     2015-08-26      1.403757   
7     7定投     0.449322       2015-06-08     2015-08-26      1.403684   
2     3定投     0.447867       2015-06-08     2015-08-26      1.403077   
10   11定投     0.451701       2015-06-08     2015-08-26      1.402237   
0     2定投     0.448598       2015-06-08     2015-08-26      1.402124   
5     6定投     0.449244       2015-06-08     2015-08-26      1.402037   
19   20定投     0.451988       2015-06-08     2015-08-26      1.401929   
20   21定投     0.451256       2015-06-08     2015-08-26      1.401919   
9    10定投     0.451326       2015-06-08     2015-08-26      1.401737   
18   19定投     0.451639       2015-06-08     2015-08-26      1.401728   
17   17定投     0.452964       2015-06-08     2015-08-26      1.401612   
12   12定投     0.451574       2015-06-08     2015-08-26      1.400466   
15   15定投     0.452362       2015-06-08     2015-08-26      1.400464   
4     4定投     0.448714       2015-06-08     2015-08-26      1.399972   
14   14定投     0.451705       2015-06-08     2015-08-26      1.399919   
3     5定投     0.448477       2015-06-08     2015-08-26      1.399513   
13   16定投     0.452202       2015-06-08     2015-08-26      1.399250   
11   13定投     0.451980       2015-06-08     2015-08-26      1.397626   

      sharpe  annualizedReturns  annualizedVolatility  variance  
27  0.375562           0.117886              0.234011  0.081217  
26  0.115626           0.056055              0.225339  0.037415  
24  0.114434           0.055799              0.225451  0.037674  
25  0.114136           0.055796              0.226009  0.038088  
1   0.111773           0.055242              0.225832  0.037117  
21  0.110109           0.054885              0.226008  0.038060  
23  0.109439           0.054744              0.226102  0.038188  
8   0.108832           0.054693              0.226891  0.037793  
6   0.108230           0.054562              0.226946  0.037533  
16  0.107895           0.054467              0.226763  0.038511  
22  0.107986           0.054429              0.226225  0.038112  
7   0.107652           0.054419              0.226836  0.037346  
2   0.107385           0.054337              0.226637  0.037666  
10  0.107717           0.054224              0.224888  0.037339  
0   0.106787           0.054209              0.226703  0.037736  
5   0.106608           0.054197              0.226975  0.037177  
19  0.106615           0.054183              0.226824  0.038835  
20  0.106669           0.054181              0.226695  0.038458  
9   0.106598           0.054157              0.226616  0.037489  
18  0.106569           0.054156              0.226665  0.038523  
17  0.106392           0.054140              0.226897  0.038363  
12  0.106705           0.053985              0.224783  0.036968  
15  0.105449           0.053985              0.227458  0.037892  
4   0.105570           0.053919              0.226569  0.037322  
14  0.105398           0.053912              0.226871  0.037612  
3   0.105291           0.053857              0.226582  0.037364  
13  0.104858           0.053822              0.227179  0.037930  
11  0.104050           0.053603              0.226838  0.037534

In [24]:
lstparams = []

# tsStart = int(trdb2py.str2timestamp('2013-05-01', '%Y-%m-%d'))
# tsStart = int(trdb2py.str2timestamp('2015-01-01', '%Y-%m-%d'))
# tsStart = int(trdb2py.str2timestamp('2015-06-01', '%Y-%m-%d'))
tsStart = int(trdb2py.str2timestamp('2018-01-01', '%Y-%m-%d'))


buy0 = trdb2py.trading2_pb2.CtrlCondition(
    name='monthdayex',
    vals=[1],
)

takeprofit0 = trdb2py.trading2_pb2.CtrlCondition(
    name='totalreturn',
    vals=[1.2],
    operators=['>='],
)

s0 = trdb2py.trading2_pb2.Strategy(
    name="normal",
    asset=trdb2py.str2asset(asset),
)

paramsaip = trdb2py.trading2_pb2.AIPParams(
    money=10000,
    type=trdb2py.trading2_pb2.AIPTT_WEEKDAY,
    day=1,
)

s0.buy.extend([buy0])
s0.takeprofit.extend([takeprofit0])
s0.paramsBuy.CopyFrom(paramsbuy)
s0.paramsSell.CopyFrom(paramssell)
s0.paramsTakeProfit.CopyFrom(paramstakeprofit)
s0.paramsAIP.CopyFrom(paramsaip)
lstparams.append(trdb2py.trading2_pb2.SimTradingParams(
    assets=[trdb2py.str2asset(asset)],
    startTs=tsStart,
    endTs=tsEnd,
    strategies=[s0],
    title='{}定投'.format(1),
))
 
lstaippnl = trdb2py.simTradings(trdb2cfg, lstparams)

trdb2py.showPNLs(lstaippnl + [pnlBaseline], toImg=isStaticImg, width=width, height=height)